In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

In [2]:
df = []
versions = ['v2.0', 'v2.1', 'v2.2', 'v3', 'v4.0', 'v4.1']
for i in range(6):
    v = versions[i]
    credits = pd.read_excel('../Input_data/LEED_credits.xlsx', sheet_name=v, header=1)
    ver = pd.read_excel('../Input_data/LEED_credits.xlsx', sheet_name=v, nrows=0).columns[0]
    title = pd.read_excel('../Input_data/LEED_credits.xlsx', sheet_name=v, nrows=0).columns[1]
    year = pd.read_excel('../Input_data/LEED_credits.xlsx', sheet_name=v, nrows=0).columns[2]
    total_pts = pd.read_excel('../Input_data/LEED_credits.xlsx', sheet_name=v, nrows=0).columns[3]
    f = {
        'ver': ver,
        'title': title,
        'year': year,
        'cred': credits,
        'total': total_pts
    }
    df.append(f)

In [3]:
def get_color(s):
    a = len(s)
    np.random.seed(a**2)
    if 'Energy' in s:
        np.random.seed(43259)
    elif 'Materials' in s:
        np.random.seed(593)
    elif 'Innovation' in s:
        np.random.seed(6953)
    return [np.random.rand()**0.5, np.random.rand()**0.5, np.random.rand()**0.5]

In [4]:
fig = plt.figure(figsize=(40, 25), dpi=400)

for ix in range(6):
    cred = df[ix]['cred']
    # gap = 3
    top = 0
    a = 500
    width = 8

    color_list = []
    for i in cred.index:
        cred.loc[i, 'bottomY'] = top
        cred.loc[i, 'leftX'] = (width + 2) * ix
        cred.loc[i, 'Height'] = a*cred.loc[i, 'Points']/df[ix]['total']
        if ix >=4 and cred.loc[i, 'Category']=='Location and Transporation':
            cred.loc[i, 'Width'] = width/2
        else:
            cred.loc[i, 'Width'] = width
        color_list.append(get_color(cred.loc[i, 'Category']))
        if cred.loc[i, 'Credit']=='LEED for Neighborhood Development Location':
            cred.loc[i, 'leftX'] += width/2
            continue
        top += a*cred.loc[i, 'Points']/df[ix]['total'] #+ gap
    cred['Color'] = color_list

    cat_mark = 0.15
    for i in cred.index:
        fig.gca().add_patch(
            plt.Rectangle(
                xy=(cred.loc[i, 'leftX'], cred.loc[i, 'bottomY']),
                width=cred.loc[i, 'Width'], height=cred.loc[i, 'Height']-1,
                fill=True,
                facecolor=cred.loc[i, 'Color'],
                edgecolor='grey',
                linewidth=1
            )
        )
        if '\\' in cred.loc[i, 'Sub-credit'] or '; ' in cred.loc[i, 'Sub-credit']:
            txt = cred.loc[i, 'Credit']
        else:
            txt = cred.loc[i, 'Credit'] + ': ' + cred.loc[i, 'Sub-credit']
        plt.text(cred.loc[i, 'leftX']+0.1, cred.loc[i, 'bottomY']+cred.loc[i, 'Height']/2+1, txt)
        
        if i==len(cred)-1:
            plt.text(cred.loc[i, 'leftX']-0.5+cat_mark, cred.loc[i, 'bottomY']+cred.loc[i, 'Height'],
                    cred.loc[i, 'Category'], rotation=90, size=12)
            cat_mark = -cat_mark
        elif cred.loc[i, 'Category']!=cred.loc[i+1, 'Category']:
            plt.text(cred.loc[i, 'leftX']-0.5+cat_mark, cred.loc[i, 'bottomY']+cred.loc[i, 'Height'],
                    cred.loc[i, 'Category'], rotation=90, size=12)
            cat_mark = -cat_mark
    ver_name = df[ix]['ver'] + ' (' + str(df[ix]['year']) + ')'
    plt.text(cred.loc[0, 'leftX'], -16, ver_name, size=20, fontweight='bold')
    plt.text(cred.loc[0, 'leftX'], -8, df[ix]['title'], size=14, fontweight='bold')

plt.xlim(-1, 59)
plt.ylim(-10, cred.loc[len(cred)-1, 'Height']+cred.loc[len(cred)-1, 'bottomY']+10)
plt.gca().invert_yaxis()
plt.axis('off')
plt.tight_layout()
fig.show()
fig.savefig('../Outputs/fig.jpg')

<ipython-input-4-1dc235fe639f>:61: UserWarning: Matplotlib is currently using module://ipykernel.pylab.backend_inline, which is a non-GUI backend, so cannot show the figure.
  fig.show()
